# Einstein Python 2020 - Day 4 - Homework

__In this Notebook, you will work with some real weather data from the weather station at NYC Central Park.__

There will be some more background information and I'll introduce a couple of useful functions.

<p style="background: green; color: white; padding: 5px; font-size: 1.5em;">Your tasks</p>

Your main work starts in the "Pre-processing our data set" section and each task is marked with a bar like the one above. You have to run some the ealier cells though to get started.

## Some meta information:

|            |                                                 |
| ---------- | ----------------------------------------------- |
| Start Date | 1869-01-01                                      |
| End Date   | 2020-05-04                                      |
| Station    | NY CITY CENTRAL PARK, NY US (GHCND:USW00094728) |

### Data Types

"Data Types" is what they call these fields on the website, _not to be confused with Python data types_.

| Key  | Description                                       |
| ---- | ------------------------------------------------- |
| TMAX | Maximum temperature                               |
| TMIN | Minimum temperature                               |
| PRCP | Precipitation                                     |
| TAVG | Average Temperature.                              |
| TSUN | Total sunshine for the period                     |
| PSUN | Daily percent of possible sunshine for the period |

I have reduced the dataset to these few arrays and uploaded it for you in NumPy's own format, so you can easily access and use it. The original data comes as `.csv` (comma separated values) file, which is fairly standard and can also be read with NumPy, Pandas or other Python tools. However, there are some complications with this specific file and I decided to spare you this pain.

Furthermore, the arrays `TAVG`, `TSUN` and `PSUN` are incomplete - they only have values in a certain range. This was already a problem in the original data - and I'm not blaming the NCEI for inconsistencies in free data spanning more than 150 years. For the most part, we will only use the other values.

<sup>1</sup>: _Formerly the National Climatic Data Center (NCDC)_

__Execute the imports-cell once:__

In [40]:
# Imports
import numpy as np

## Load data

Let's start by loading the data. You should have downloaded the file `weather.npz` from the [Einstein Python 2020 mini website](https://python.tyto.xyz/) in the Homework section of Day 4. Place this file in the same directory as this Notebook.

__Note:__ `.npz` files are NumPy's own file format to store multiple arrays. It's the big sister of `.npy` which stores just a single array. The corresponding functions are [`np.save()`](https://numpy.org/doc/stable/reference/generated/numpy.save.html) and [`np.savez()`](https://numpy.org/doc/stable/reference/generated/numpy.savez.html)  to save single or multiple arrays, respectively. The function [`np.load()`](https://numpy.org/doc/stable/reference/generated/numpy.load.html), which we are using here, can handle both types of files, but behaves slightly different.

In [42]:
# Open the data file
weather_data = np.load('weather.npz')
# Which variable are included?
print("Files within the weather.npz archive:")
print(weather_data.files)

Files within the weather.npz archive:
['STATION', 'NAME', 'DATE', 'TMIN', 'TMAX', 'TAVG', 'PRCP', 'PSUN', 'TSUN']


In [44]:
# Some basic information:
print("Station Name:", weather_data['NAME'])
print("Station Code:", weather_data['STATION'])

Station Name: NY CITY CENTRAL PARK, NY US
Station Code: USW00094728


As you can see, there are several arrays stored in `weather.npz`. Because that is basically a zip-archive of `.npy` files, the terminology also speaks of "files". But we get a nice _dictionary-like_ interface to load individual arrays.

For ease of use, let's store the interesing arrays in nicely named variables (you will see further down, why I used the `_all` suffix):

In [58]:
# Make easier Numpy arrays
date_all = weather_data['DATE']
tmin_all = weather_data['TMIN']
tmax_all = weather_data['TMAX']
prcp_all = weather_data['PRCP']

## A first look at our data

All of these arrays should be one-dimensional and have the same lengths. Elements __at the same index__ correspond to the same day.

Let's take a quick look at that:

In [64]:
print("date: ndim = {}, shape = {}".format(date_all.ndim, date_all.shape))
print("tmin: ndim = {}, shape = {}".format(tmin_all.ndim, tmin_all.shape))
print("tmax: ndim = {}, shape = {}".format(tmax_all.ndim, tmax_all.shape))
print("prcp: ndim = {}, shape = {}".format(prcp_all.ndim, prcp_all.shape))

date: ndim = 1, shape = (55275,)
tmin: ndim = 1, shape = (55275,)
tmax: ndim = 1, shape = (55275,)
prcp: ndim = 1, shape = (55275,)


We can also see if how the date range actually looks like:

In [65]:
print("First day:", date_all[0])
print("Last day: ", date_all[-1])

First day: 1869-01-01
Last day:  2020-05-03


Unfortunately, even for these almost complete data sets, there are some missing values. Those values are included as `np.nan` in the arrays. NumPy gives us a function `np.isnan()` so check which values are "not a number".

__Note:__ Due to the nature of `nan` values, a comparison like `value == np.nan` is _not_ reliable!

See here:

In [67]:
np.isnan(tmax_all)

array([False, False, False, ..., False, False, False])

Okay, that is not super helpful because (luckily) the now boolean output array is not printed with all 55275 values!

But we can use it, so see which dates are actually affected, hoping it's much less. I'm using the `display()` function here, which is similar to `print()` but in Jupyter Notebooks often produces a nicer output - try the difference yourself, if you want!

In [70]:
print("NaN in tmax_all:")
display(date_all[np.isnan(tmax_all)])
print("NaN in tmin_all:")
display(date_all[np.isnan(tmin_all)])
print("NaN in prcp_all:")
display(date_all[np.isnan(prcp_all)])

NaN in tmax_all:


array(['1869-05-02', '1869-05-03', '1869-05-04', '1869-05-05',
       '1869-05-06', '1869-05-07', '1869-05-08'], dtype='datetime64[D]')

NaN in tmin_all:


array(['1869-05-02', '1869-05-03', '1869-05-04', '1869-05-05',
       '1869-05-06', '1869-05-07', '1869-05-08'], dtype='datetime64[D]')

NaN in prcp_all:


array([], dtype='datetime64[D]')

That's good. We have only a few temperatures missing in May of 1869, which happens to be the first year in our dataset. Also, you have seen that we have another "incomplete" year, which is of course the one we are currently in, 2020.

For working with the `date` array, we need some additional info first...

## `datetime64` - The data type of the "date" array

Working with dates on computers always is a challenge. There are tons of different ideas, how to represent dates for different use cases. The most common one nowadays is the UNIX timestamp, which is simply the number of seconds since January 1st, 1970. Odd? Yes, but useful in many cases. For our dates, this is less helpful. Luckily, there is a good NumPy solution, the dtype `datetime64` - still "experimental", but really good for our use case.

You can find the full documentation here: https://numpy.org/doc/stable/reference/arrays.datetime.html

`datetime64` comes with several precisions, for years, months, days, hours, seconds, milliseconds, and so on. You may have noticed that the dtype of our `date_all` array above was indicated as `datetime64[D]`, which of course indicates the precision as "day". Often, NumPy will choose the best presision for the date and time you need.

To create a single date, you can write it as `str` in ISO format (`YYYY-MM-DD`) and use the `np.datetime64()` function to convert it. You can be as precise as you need it by just leaving out the less precise parts.

Some examples:

In [88]:
# Albert Einstein's birthday, 14 March 1879:
bday = np.datetime64('1879-03-14')
byear = np.datetime64('1879')
# Note the different outputs, indicating the time unit or precision
display(bday)
display(byear)
# The `str` representation of datetime64 is more human readable.
# `print()` uses that automatically, or you convert it with `str()`
print(bday)
print("Albert Einstein was born in " + str(byear))
print('--------------------')
# Now we can check the weather at Einstein's birthday (of course in NY, not where he was born)
# We use boolean indexing here. Check it first with the date_all:
display(date_all[date_all == bday])
# Note that boolean indexing always returns an array, even if there is only one value or none at all.
# As we know that there was a single day, we can just take the first element of the array:
print("Einstein's Birthday:")
print(bday)
print("Min temperature in NYC: {}".format(tmin_all[date_all == bday][0]))
print("Max temperature in NYC: {}".format(tmax_all[date_all == bday][0]))
print("Precipitation in NYC:   {}".format(prcp_all[date_all == bday][0]))


numpy.datetime64('1879-03-14')

numpy.datetime64('1879')

1879-03-14
Albert Einstein was born in 1879
--------------------


array(['1879-03-14'], dtype='datetime64[D]')

Einstein's Birthday:
1879-03-14
Min temperature in NYC: 39.0
Max temperature in NYC: 56.0
Precipitation in NYC:   0.0


An important note about the `datetime64` type is that it always represents a _single_ point in time. If you think about a day or even a year, you might think more about it as a period. The `datetime64` type indicates the start of that period. That is good to know in comparisons:

In [109]:
# A year is equal to January 1st at midnight (left the year, right with millisecond precision):
np.datetime64('2010') == np.datetime64('2010-01-01 00:00:00.000')

True

In [120]:
# an array of dates:
some_days = np.array(['1872-02-22', '1953-12-15', '1985-07-10', '1993-11-01', '2020-04-30'], dtype='datetime64[D]')
# an array of values can be compared to a single value:
display(some_days > np.datetime64('2000'))
# select some_days within a range, stepwise:
# a boolean array - note the () which are necessary to overcome the order of operators:
# also note the different use of inclusive (>=) and exclusive (<) comparisons. Try variations!
within_range = (some_days >= np.datetime64('1953-12-15')) & (some_days < np.datetime64('1993-11-01'))
display(within_range)
# Use boolean indexing
display(some_days[within_range])

array([False, False, False, False,  True])

array([False,  True,  True, False, False])

array(['1953-12-15', '1985-07-10'], dtype='datetime64[D]')

## Alternatives to boolean indexing

### `np.where()`

Sometimes we need the numeric indexes of `True` values instead of using the entire boolean array. `np.where()` returns that. With one perk: As it works on all kinds of arrays, it always returns a `tuple` of arrays. Each array in the tuple has the indexes of all true'ish values along one dimension.

We need a quick 2D-example to show that in action:

In [97]:
# Generate a 3x3 matrix. You can find out more about numpy.reshape in the official documentation:
mat = np.arange(9).reshape((3,3))
display(mat)
# Display the tuple
display(np.where(mat == 5))
# Unpack the tuple into two separate variables:
i0, i1 = np.where(mat == 5)
# show the FIRST - index [0] - position where mat is 5:
print(f"mat[{i0[0]}, {i1[0]}] is equal to 5")
# Another example:
i0, i1 = np.where(mat % 3 == 0)
for k in range(i0.size):
    print(f"mat[{i0[k]}, {i1[k]}] = {mat[i0[k], i1[k]]} is a multiple of 3")

array([[0, 1, 2],
       [3, 4, 5],
       [6, 7, 8]])

(array([1]), array([2]))

mat[1, 2] is equal to 5
mat[0, 0] = 0 is a multiple of 3
mat[1, 0] = 3 is a multiple of 3
mat[2, 0] = 6 is a multiple of 3


Of course, our arrays are one-dimensional. So we can just take the first array out of the tuple returned by `np.where()`.

The above example of Einstein's Birthday could look like this:

In [105]:
# Note the two [0] at the end of the next line.
# The first 0 gets the first array in the tuple,
# the second 0 get the first (and only) element in that array:
bday_index = np.where(date_all == bday)[0][0]
print(f"The {bday} has the index {bday_index} in our full dataset.")

# Now we have single integer as index and don't need the [0] in the following lines:
print("Min temperature in NYC: {}".format(tmin_all[bday_index]))
print("Max temperature in NYC: {}".format(tmax_all[bday_index]))

The 1879-03-14 has the index 3724 in our full dataset.
Min temperature in NYC: 39.0
Max temperature in NYC: 56.0


The `np.where()` function works for any number of true values within a boolean array, including zero, one or many.

That will again come in handy later!

### `np.searchsorted()`

Another great method to find a single value in a _sorted_ array, is the `np.searchsorted()` function. It's vitally important that the original array is sorted, but then it's one of the fastest methods we have, using what is called "binary search".

Of course, this is most useful for our date array. Let's just try it with the value we already know:

In [108]:
bday_index = np.searchsorted(date_all, bday)
print(f"The {bday} has the index {bday_index} in our full dataset.")

The 1879-03-14 has the index 3724 in our full dataset.


## Pre-processing our data set

<p style="background: green; color: white; padding: 5px; font-size: 1.5em; font-weight:bold;">Task 1</p>

As we have seen before, some data is missing in the maximum and minimum temperature arrays and we have the incomplete current year 2000.

Let's make things a little easier and cut all of our arrays "shorter", such that we have the 150 years with continuous data from 1870 to 2019 (including both).

You know at least two ways of doing so by now. Choose one:

* Create a boolean array `consistent_bool` which is `True` for all dates in that range. The range of interest is then `date_all[consistent_bool]`.
* Find the indexes `consistent_start` and `consistent_stop`, such that `date_all[consistent_start:consistent_stop]` starts with 1870-01-01 and ends with 2019-12-31.

__Goal:__ In the following parts of the notebook, I will assume that you have the arrays `date`, `tmin`, `tmax` and `prcp` of equal length.

In [140]:
# Boolean version
consistent_bool = (data['DATE'] >= np.datetime64('1870')) & (data['DATE'] < np.datetime64('2020'))
date = date_all[consistent_bool]
tmin = tmin_all[consistent_bool]
tmax = tmax_all[consistent_bool]
prcp = prcp_all[consistent_bool]

In [141]:
# Index version (faster)
consistent_start = np.searchsorted(date_all, np.datetime64('1870'))
consistent_stop = np.searchsorted(date_all, np.datetime64('2020'))
date = date_all[consistent_start:consistent_stop]
tmin = tmin_all[consistent_start:consistent_stop]
tmax = tmax_all[consistent_start:consistent_stop]
prcp = prcp_all[consistent_start:consistent_stop]

When you're done, check if the sizes are correct:

In [147]:
if (date.size == 54786):
    print("Your date array has the correct size.")
else:
    print("Something went wrong. Your date array should have 54786 elements, bus it has: {date.size}")
# And we compare the others to date:
print("date.size == tmin.size :", date.size == tmin.size)
print("date.size == tmin.size :", date.size == tmax.size)
print("date.size == tmin.size :", date.size == prcp.size)

Your date array has the correct size.
date.size == tmin.size : True
date.size == tmin.size : True
date.size == tmin.size : True


<p style="background: limegreen; color: white; padding: 5px; font-size: 1.5em;">Bonus Task (optional)</p>

If you write `%%timeit` at the beginning of a cell (on a line by itself), Python runs that cell a couple of times and shows you a statistic of how long each run took. Implement both of the above approaches and compare their timing.

Be aware: Variables assigned in a `%%timeit`-cell will _not_ exist afterwards.

__Examples__

```python
%%timeit
# Sum, then divide
np.sum(np.arange(1000000)) / 2
# Output will be like:
# 1.17 ms ± 7.49 µs per loop (mean ± std. dev. of 7 runs, 1000 loops each)
```

```python
%%timeit
# Divide each element, then sum
np.sum(np.arange(1000000) / 2)
# Output will be like:
# 3.51 ms ± 41.1 µs per loop (mean ± std. dev. of 7 runs, 100 loops each)
```

In [347]:
# no solution needed

# A few individual values

<p style="background: green; color: white; padding: 5px; font-size: 1.5em; font-weight:bold;">Task 2</p>

You have seen a lot by now. Let's do some rather simple things:

1) Print the minimimum and maximum temperatures at __your birthday__?

In [183]:
bday = np.datetime64('1879-03-14') # Einstein's birthday, not mine
bday_index = np.searchsorted(date, bday)
print(f"Temperature on my birthday in NY ranged from {tmin[bday_index]} to {tmax[bday_index]}.")

Temperature on my birthday in NY ranged from 39.0 to 56.0.


2) Did it rain on your birthday? If yes, how much?

In [184]:
if prcp[bday_index] > 0:
    print(f"On my birthay, there were {prcp[bday_index]} inch of precipitation.")
else:
    print("It did not rain on my birthay.")    

It did not rain on my birthay.


3) To test a rainy and a non-rainy day, you can try Christmas day (December 25th) in 1985 or 1986.  
Does your code work if you just change the date at one position?

You can now tell your family/roommates how the wether was on their birthdays... but you don't have to ;-)

3) What was the highest temperature during the entire 150 years?

In [182]:
np.max(tmax)

106.0

4) When was the coldest day in the same range? And what was the lowest temperature?

__Hint:__ Compare the minimum of tmin with all values of tmin. Then use boolean indexing or `np.where()`.

In [179]:
# Boolean:
print(date[np.min(tmin) == tmin][0], "was the coldest day.")
# Integer index, split for clarity and to avoid finding the minimum twice:
coolest_day = np.where(np.min(tmin) == tmin)[0][0]
print(date[coolest_day], "was the coolest. It was", tmin[coolest_day], "that day.")

1934-02-09 was the coolest day.
1934-02-09 was the coolest. It was -15.0 that day.


5) There were 31 days in these 150 years with maximal temperatures above 100 degrees (101 or higher). Can you find out the dates?

In [358]:
date[tmax > 100]

array(['1881-09-07', '1918-08-07', '1930-07-21', '1933-07-31',
       '1934-06-29', '1936-07-09', '1936-07-10', '1944-08-05',
       '1944-08-11', '1948-08-26', '1948-08-27', '1949-07-04',
       '1953-07-18', '1953-09-02', '1957-07-22', '1966-06-27',
       '1966-07-03', '1966-07-13', '1977-07-19', '1977-07-21',
       '1980-07-20', '1980-07-21', '1991-07-21', '1993-07-09',
       '1993-07-10', '1995-07-15', '1999-07-05', '1999-07-06',
       '2001-08-09', '2010-07-06', '2011-07-22'], dtype='datetime64[D]')

6) Similarly, you can find the _number of days_ with minimal temperatures below 0 degrees. It should be 59.

In [363]:
np.sum(tmin < 0)

59

# Look at specific ranges

<p style="background: green; color: white; padding: 5px; font-size: 1.5em; font-weight:bold;">Task 3</p>

The additional challenge in the next exercises is to use a range of dates and don't mess up the indexes.

__Hint:__ First create shorter arrays of all you need and then index into those.

1) What were the highest and lowest temperatures in your birth year and when did they happen?

It's okay to use "hard-coded" dates for the beginning and the end first, like:

```python
byear_begin = np.datetime64('1879-01-01')
# ...
```

In [234]:
byear_beg = np.datetime64('1879-01-01')
byear_end = np.datetime64('1880-01-01')
# Calculate the indexes:
byear_start = np.searchsorted(date, byear_beg)
byear_stop = np.searchsorted(date, byear_end)
# You can get shorter arrays first:
y_date = date[byear_start:byear_stop]
y_tmin = tmin[byear_start:byear_stop]
y_tmax = tmax[byear_start:byear_stop]
# And then search for extrema:
y_coldest = np.min(y_tmin)
y_hottest = np.max(y_tmax)
# And get the indexes:
y_coldest_ind = np.where(y_coldest == y_tmin)[0][0]
y_hottest_ind = np.where(y_hottest == y_tmax)[0][0]
# Get the dates:
y_coldest_day = y_date[y_coldest_ind]
y_hottest_day = y_date[y_hottest_ind]
# Print:
print(f"The coldest day in Albert's birthyear 1879 was {y_coldest_day} with {y_coldest} degrees.")
print(f"The hottest day in Albert's birthyear 1879 was {y_hottest_day} with {y_hottest} degrees.")

The coldest day in Albert's birthyear 1879 was 1879-01-03 with -4.0 degrees.
The hottest day in Albert's birthyear 1879 was 1879-07-16 with 98.0 degrees.


2) How much did it rain during your birthyear?

Use `np.sum()` and the correct range of `prcp`.

In [235]:
# re-using the indexes from above, we just need to applyto prcp:
y_prcp = prcp[byear_start:byear_stop]
y_rain_total = np.sum(y_prcp)
print(f"The total amount of precipitation in 1879 was {y_rain_total} inches.")

The total amount of precipitation in 1879 was 39.03 inches.


3) How many rainy days (`prcp[_index_] > 0`) did your birthyear have?

__Hint:__ You can use `np.sum()` with a boolean array and it will count the `True` values.

In [239]:
# Based on the previous cell again, we can just count rainy days:
y_rainy_days = np.sum(y_prcp > 0)
# Lets also count total days:
y_total_days = y_prcp.size
print(f"In 1879 it rained on {y_rainy_days} of {y_total_days} ({y_rainy_days/y_total_days:.1%}).")

In 1879 it rained on 125 of 365 (34.2%).


## Manipulating `datetime64` values

We can also get the year for a date by converting it to a coarser unit:

```python
bday = np.datetime64('1879-03-14')
byear = bday.astype('datetime64[Y]')
```

We could also take the `str` representation and cut off the end (`str` supports indexing just like `list`):

```python
bday_str = str(bday)      # '1879-03-14'
byear_str = bday_str[:4]  # '1879'
byear = np.datetime64(byear_str)
```

With that technique, it's also pretty easy to create arbitrary dates, like Independence day in Einstein's birthyear:

```python
indep_day = np.datetime64(byear_str + '-07-04')
```

And because we can convert a `str` like `'1879'` into an integer `1879`, we can also manipulate it relatively easy. We just have to convert data type back and forth a little:

```python
bday = np.datetime64('1879-03-14')
bday_str = str(bday)
# Einstein's 11th birthday, in many steps:
byear_str = bday_str[:4]                            # '1879'
byear_int = int(byear_str)                          # 1879
byear_plus_11_int = byear_int + 11                  # 1890
byear_plus_11_str = str(byear_plus_11_int)          # '1890'
bday_plus_11_str = byear_plus_11_str + bday_str[4:] # '1890-03-14'
bday_plus_11 = np.datetime64(bday_plus_11_str)      # datetime64('1890-03-14')
# If it's just for printing, we could have used the str version of course:
print("Einstein's became 11 years old on:", bday_plus_11)
# And in fewer steps:
display(np.datetime64(str(int(bday_str[:4])+11) + bday_str[4:]))
```

### `timedelta64` - differences between dates and times

There is another datatype, `timedelta64` - the sister of `datetime64`. It's used for some arithmetics on `datetime64`-values. For example, the difference between two `datetime64`s will be a `timedelta64`, or you can add a `timedelta64` to a date - certain conditions apply. It's also described on the same page in the documentation.

__Examples__

```python
# The day one week after your birthday:
bday + np.timedelta(7, 'D')
# The year your 16th birthday happened:
byear + np.timedelta(1, 'Y')
# Even your age in days becomes simple:
np.datetime('2020-05-11') - bday
```

What the documentation is lacking is that `timedelta64` can be converted into other units and into `int` easily:

```python
# As timedelta64
age_days = np.datetime('2020-05-11') - bday   # timedelta64(51558,'D')
age_years = age_days.astype('timedelta64[Y]') # timedelta64(141,'Y')
# The integer numbers:
age_days_int = age_days.astype(int)           # 51558
age_days_int = age_days.astype(int)           # 141
```

Also, there are some things that remain impossible with `timedelta64`, mainly because there are non-linear relationships between days and years/months. Remember that internally these dates are "just numbers" and because a month or a year can have different numbers of days, adding those units together is not "just adding". It might be added in the future (I'd love that) but for now, NumPy remains dumb in this aspect.

__*NON-WORKING* Examples__

```python
# Will NOT work:
bday + np.timedelta64(1, 'Y')
# Will NOT work:
bday + np.timedelta64(1, 'M')
```

Of course, you can usually add values within the same unit and also combinations of days with everything shorter, as well as months and years together work:

__This works__

```python
bday.astype('datetime64[M]') + np.timedelta64(1, 'Y') # datetime64('1880-03'), note the month-precision!
bday.astype('datetime64[M]') + np.timedelta64(1, 'M') # datetime64('1879-04')
```

Now, we __can__ use all of this together to "transport" the birthday 11 years into the future, but we have to combine a couple of things:

```python
bday = np.datetime64('1879-03-14')
bmonth = bday.astype('datetime64[M]')
bmonth_plus_11 = bmonth + np.timedelta64(11, 'Y')
# We also need the "distance" of bday to the beginning of the month,
# Note that this is timedelta64(13,'D'), not 14 days:
bday_in_month = bday - bmonth
# At this point, bmonth_plus_11 == datetime64('1890-03')
# The next line will automatically convert it to datetime64('1890-03-01') before adding days:
bday_plus_11 = bmonth_plus_11 + bday_in_month
# Or once again in one line:
bday_plus_11 = (bday.astype('datetime64[M]') + np.timedelta64(11, 'Y')) + (bday - bday.astype('datetime64[M]'))
```

The parentheses are necessary in the last line. Also, it is not possible to "cut out" the plus and minus `bday.astype('datetime64[M]')`. And this is one of the reasons, I was so insisting on data types in the first classes... it never leaves you again.

Two functions that you may want to use (but don't need to) are `np.datetime_data()` or `np.datetime_as_string()`. Look into the help if you want.

<p style="background: limegreen; color: white; padding: 5px; font-size: 1.5em;">Bonus Task (optional)</p>

Calculate your own age in days, months, seconds?

Remember when some uncle did that at a birthday party? Probably calculated on a piece of paper and not unlikely with some a mistake (again: leap years). You can do it better now - and faster.

If you want to have a dynamic "now" or "today", take one of the following. You have to `import time`, a builtin Python module to get the current UNIX time (seconds since "Epoch", the start of 1970, possibly with decimals for milli-/micro-second or even smaller).

```python
import time
epoch = np.datetime64('1970')
unix_time = np.timedelta64(int(time.time()), 's')
now = epoch + unix_time
today = epoch + unit_time.astype('timedelta64[D]')
```

In [280]:
import time

bday = np.datetime64('1985-07-10')
epoch = np.datetime64('1970')
unix_time = np.timedelta64(int(time.time()), 's')
now = epoch + unix_time
today = epoch + unix_time.astype('timedelta64[D]')
print("Age in days:", today - bday)
print("Age in seconds:", now - bday)

Age in days: 12724 days
Age in seconds: 1099380937 seconds


<p style="background: green; color: white; padding: 5px; font-size: 1.5em; font-weight:bold;">Task 4</p>

1) Copy your code from Task 3.1 (extreme temperatures in your birthyear).  
Adapt it to calculate the `byear` from your birthday `bday` and show the temperatures of that year. Try different dates, too.

In [293]:
bday = np.datetime64('1879-03-14')
byear_beg = bday.astype('datetime64[Y]')
byear_end = bday.astype('datetime64[Y]') + np.timedelta64(1, 'Y')
print("Check:", byear_beg, byear_end)
# --- everything below here remains unchanged ---
# Calculate the indexes:
byear_start = np.searchsorted(date, byear_beg)
byear_stop = np.searchsorted(date, byear_end)
# You can get shorter arrays first:
y_date = date[byear_start:byear_stop]
y_tmin = tmin[byear_start:byear_stop]
y_tmax = tmax[byear_start:byear_stop]
# And then search for extrema:
y_coldest = np.min(y_tmin)
y_hottest = np.max(y_tmax)
# And get the indexes:
y_coldest_ind = np.where(y_coldest == y_tmin)[0][0]
y_hottest_ind = np.where(y_hottest == y_tmax)[0][0]
# Get the dates:
y_coldest_day = y_date[y_coldest_ind]
y_hottest_day = y_date[y_hottest_ind]
# Print:
print(f"The coldest day in Albert's birthyear {byear_beg} was {y_coldest_day} with {y_coldest} degrees.")
print(f"The hottest day in Albert's birthyear {byear_beg} was {y_hottest_day} with {y_hottest} degrees.")

Check: 1879 1880
The coldest day in Albert's birthyear 1879 was 1879-01-03 with -4.0 degrees.
The hottest day in Albert's birthyear 1879 was 1879-07-16 with 98.0 degrees.


2) Try the same thing for the month you were born in.  
Then expand it to show the same values for the months before and after.

__Note:__ If you were born in January or December, that might be more tricky than it seems at first glance. Maybe pretend to be Einstein first. Everyone can then think about what needs to be changed to make is work in January/December cases as well.

In [369]:
bday = np.datetime64('1879-03-14')
# now some shorter code, but essentially the same
bmonths = bday.astype('datetime64[M]')
# I decided to put everything in a loop:
for delta_month in [0, -1, 1]:
    # start and stop indexes
    m_start = np.searchsorted(date, bmonth + np.timedelta64(delta_month, 'M'))
    m_stop = np.searchsorted(date, bmonth + np.timedelta64(delta_month + 1, 'M'))
    m_date = date[m_start:m_stop]
    m_tmin = tmin[m_start:m_stop]
    m_tmax = tmax[m_start:m_stop]
    # Instead of calculating the minimum and using np.where(),
    # I use np.argmax() and np.argmin() which return the index
    # of the maximum and minimum, respectively:
    m_coldest_ind = np.argmin(m_tmin)
    m_hottest_ind = np.argmax(m_tmax)
    if delta_month == 0:
        print(f"In Albert's birthmonth {bmonth},")
    elif delta_month == -1:
        print(f"\nIn the month before,")
    else:
        print(f"\nIn the following month,")
    print(f"the coldest day was {m_date[m_coldest_ind]} with {m_tmin[m_coldest_ind]} degrees and")
    print(f"the hottest day was {m_date[m_hottest_ind]} with {m_tmax[m_hottest_ind]} degrees.")


In Albert's birthmonth 1879-03,
the coldest day was 1879-03-01 with 18.0 degrees and
the hottest day was 1879-03-10 with 69.0 degrees.

In the month before,
the coldest day was 1879-02-15 with 9.0 degrees and
the hottest day was 1879-02-26 with 52.0 degrees.

In the following month,
the coldest day was 1879-04-05 with 25.0 degrees and
the hottest day was 1879-04-30 with 76.0 degrees.


3) Now you should be equipped to split a year into 12 months. Use your birthyear again and print the amount of rain in every month.

__Hint:__ You can start simple and try it for one month at a time, THEN think about how to get to each month from the beginning of the year with a `timedelta` and enclose you code with a `for`-loop like this:

```python
# The '...' must be replaced by your code of course!
bday = np.datetime64('1879-03-14')
byear = bday.astype('datetime64[Y]')
for delta_month in range(0, 12): # integers from 0 to 11
    # This month's indexes into date, tmin, tmax, prcp:
    month = byear + ...
    m_start = np.searchsorted(date, ...)
    m_stop = ...
    ...
```

If you want to print `Jan` or `Aug` instead of `0` or `7`, here is a small gift for you:

```python
months_names = ['Jan', 'Feb', 'Mar', 'Apr', 'May', 'Jun', 'Jul', 'Aug', 'Sep', 'Oct', 'Nov', 'Dec']
```

In [315]:
months_names = ['Jan', 'Feb', 'Mar', 'Apr', 'May', 'Jun', 'Jul', 'Aug', 'Sep', 'Oct', 'Nov', 'Dec']

bday = np.datetime64('1879-03-14')
byear = bday.astype('datetime64[Y]')
print(f"Precipitation in Albert's birthyear {byear}:")
for delta_month in range(0, 12): # integers from 0 to 11
    # This month's indexes into date, tmin, tmax, prcp:
    month = byear + np.timedelta64(delta_month, 'M')
    m_start = np.searchsorted(date, month)
    m_stop = np.searchsorted(date, month + np.timedelta64(1, 'M'))
    # Finally, calculate the amount of rain:
    m_rain = np.sum(prcp[m_start:m_stop])
    # And print:
    print(f"{months_names[delta_month]}: {m_rain:.2f} inches")

Precipitation in Albert's birthyear 1879:
Jan: 2.63 inches
Feb: 2.02 inches
Mar: 3.41 inches
Apr: 4.33 inches
May: 2.02 inches
Jun: 3.15 inches
Jul: 3.58 inches
Aug: 7.95 inches
Sep: 2.37 inches
Oct: 0.43 inches
Nov: 2.20 inches
Dec: 4.94 inches


<p style="background: limegreen; color: white; padding: 5px; font-size: 1.5em;">Bonus Task (optional)</p>

Similarly, you can print out the weather on all your birthdays from whenever you were born (the number of iterations in the loop then depends on your age) until 2019. This might be easier to solve by converting dates to `str` to pick the same day every year, as shown above.

In [346]:
# Using Independence day of the last 40 years:
bday = np.datetime64('1980-07-04')
byear = int(str(bday.astype('datetime64[Y]')))
# Now we loop over years (as integers):
for y in range(byear, 2020):
    y_bday = np.datetime64(str(y) + str(bday)[4:], 'D')
    y_bday_ind = np.searchsorted(date, y_bday)
    rain_str = f"{prcp[y_bday_ind]} inch of" if prcp[y_bday_ind] else 'no'
    print(f"{y_bday}: {tmin[y_bday_ind]} to {tmin[y_bday_ind]} degree and {rain_str} rain.")

1980-07-04: 70.0 to 70.0 degree and no rain.
1981-07-04: 70.0 to 70.0 degree and 1.76 inch of rain.
1982-07-04: 60.0 to 60.0 degree and no rain.
1983-07-04: 78.0 to 78.0 degree and no rain.
1984-07-04: 71.0 to 71.0 degree and 0.01 inch of rain.
1985-07-04: 68.0 to 68.0 degree and no rain.
1986-07-04: 55.0 to 55.0 degree and no rain.
1987-07-04: 74.0 to 74.0 degree and no rain.
1988-07-04: 65.0 to 65.0 degree and no rain.
1989-07-04: 66.0 to 66.0 degree and no rain.
1990-07-04: 71.0 to 71.0 degree and no rain.
1991-07-04: 63.0 to 63.0 degree and no rain.
1992-07-04: 60.0 to 60.0 degree and 0.33 inch of rain.
1993-07-04: 73.0 to 73.0 degree and no rain.
1994-07-04: 69.0 to 69.0 degree and no rain.
1995-07-04: 64.0 to 64.0 degree and no rain.
1996-07-04: 63.0 to 63.0 degree and 0.04 inch of rain.
1997-07-04: 71.0 to 71.0 degree and no rain.
1998-07-04: 68.0 to 68.0 degree and 0.05 inch of rain.
1999-07-04: 79.0 to 79.0 degree and no rain.
2000-07-04: 70.0 to 70.0 degree and no rain.
2001-

# Aggregate data

In the end, we want to combine data across ranges and then continue using this aggregated data to answer further quesions - which is mostly up to your own creativity.

<p style="background: green; color: white; padding: 5px; font-size: 1.5em; font-weight:bold;">Task 5</p>

1) First, lets combine `tmin` and `tmax`, such that we get an "average" temperature `tavg` for every day. This might not be exactly the average that meteorologist use, but unfortunately the data set didn't include average temperatures for most of the 150 years.

Just calculate the mean of maximum and minimum temperature for every day - which is a quick _element-wise_ operation with NumPy. Remember that the mean of two numbers is their sum devided by 2:

```python
avg = (a + b) / 2
```

In [348]:
tavg = (tmin + tmax) / 2

2) You can now calculate the average temperature for every of the 150 years. Do this in a `for`-loop and collect all results in a `list`-variable `years_tavg`.

__Hint:__ You need to create an empty list before the loop starts. Then you can use `years_tavg.append(_value_)` to fill it with values. When the loop is done, you should convert `years_tavg` into a NumPy array:

```python
years_tavg = np.array(years_tavg)
```

I have started the loop for you, using the `np.arange()`-function to create an array of all our years.

__Note:__ If you use `np.searchsorted` for the start/stop indexes, you might wonder what happens for the last year - there is no `'2020-01-01'` in `date`. `np.searchsorted` will still return the correct index, because it does not return the index of an element found (like `list.index()` for example) but the position where the given element should be inserted to keep the array sorted.

In [372]:
years = np.arange('1870', '2020', dtype='datetime64[Y]')
years_tavg = []

for year in years:
    # year is a datetime64 value now:
    #display(year)
    # Find start and stop indexes for this year:
    y_start = np.searchsorted(date, year)
    y_stop = np.searchsorted(date, year + np.timedelta64(1, 'Y'))
    # Calculate the mean of tavg in this year:
    y_tavg = np.mean(tavg[y_start:y_stop])
    # Append to the list:
    years_tavg.append(y_tavg)

years_tavg = np.array(years_tavg)
display(years_tavg)

array([53.76027397, 51.40410959, 51.37021858, 50.9109589 , 51.35890411,
       49.52739726, 52.        , 52.87123288, 53.73424658, 52.30410959,
       52.95491803, 52.35205479, 51.80410959, 50.25205479, 52.2636612 ,
       50.71643836, 51.37534247, 51.04657534, 49.46721311, 52.93424658,
       53.01369863, 54.22739726, 52.24590164, 50.83013699, 53.10273973,
       53.16575342, 53.65710383, 53.70958904, 55.15342466, 54.09589041,
       54.27808219, 52.5890411 , 53.09452055, 53.13287671, 50.93989071,
       53.59726027, 55.09726027, 53.03835616, 55.1079235 , 53.73561644,
       53.65205479, 53.58630137, 52.77595628, 55.07260274, 52.10273973,
       53.49863014, 52.26775956, 50.83424658, 53.28493151, 53.85753425,
       52.31284153, 54.95205479, 53.60273973, 52.99726027, 51.95765027,
       53.47534247, 51.3369863 , 53.48082192, 53.59016393, 54.1890411 ,
       54.55890411, 55.87671233, 55.21038251, 54.32328767, 53.12054795,
       53.13013699, 53.49180328, 54.54246575, 55.28630137, 54.72

3) Now you can use `years` and `years_tavg` to answer another bunch of interesing questions, like

*   Which year was the hottest on average? And how hot was that?
*   Was the hottest day during the hottest year?
*   What is the standard deviation (`np.std`) of yearly average temperatures? Which years were above or below that, if any?
*   (How much) Did the average temperature increase over 150 years?  
    _You may want to calculate averages for each decade to get a glimps at this._

If you add some more aggregating above, you can ask even more complex questions:

*   Is the hottest month (highest mean tavg) every year the same?
*   How much precipitation fell in the 10 hottest years compared to the 10 coldest years?
*   Given the maximum, minimum and average temperature per year (and maybe the standard deviation of the average temperature across the year), which of these values was most diffent between the 50-year-ranges 1870-1919, 1920-1969 and 1970-2019?

And many more... it's now up to you to further explore this data set.

In [381]:
# Hottest year:
y_hot_ind = np.argmax(years_tavg)
print(f"The hottest year was {years[y_hot_ind]} with an average of {years_tavg[y_hot_ind]:.1f} degrees.")

The hottest year was 2012 with an average of 57.4 degrees.


In [386]:
# Hottest day of hottest year:
y_start = np.searchsorted(date, years[y_hot_ind])
y_stop = np.searchsorted(date, years[y_hot_ind] + np.timedelta64(1, 'Y'))
# This is the index into the days of the hottest year:
d_hot_ind_year = np.argmax(tmax[y_start:y_stop])
# We can just add y_start to obtain the intex into date, tmax etc.
d_hot_ind = d_hot_ind_year + y_start
print(f"The hottest day in {years[y_hot_ind]} was {date[d_hot_ind]} with a max. of {tmax[d_hot_ind]} degrees.")
# Alternatively, we could have use it to get the value out of this years dates
# by using an index for the year first and then the d_hot_ind_year afterward:
d_hot = date[y_start:y_stop][d_hot_ind_year]
# but then we also need to use this other values, too:
d_hot_tmax = tmax[y_start:y_stop][d_hot_ind_year]
print(f"The hottest day in {years[y_hot_ind]} was {d_hot} with a max. of {d_hot_tmax} degrees.")
print(f"This was the day at index {d_hot_ind_year} within this year and {d_hot_ind} in our full data set.")

The hottest day in 2012 was 2012-07-18 with a max. of 100.0 degrees.
The hottest day in 2012 was 2012-07-18 with a max. of 100.0 degrees.
This was the day at index 199 within this year and 52063 in our full data set.
